In [1]:
import seaborn
import pandas as pd
import wandb
import pandas_profiling

In [2]:
run = wandb.init(project="exercise_4", save_code=True)

wandb: Currently logged in as: geodego (use `wandb login --relogin` to force relogin)
wandb: wandb version 0.12.9 is available!  To upgrade, please run:
wandb:  $ pip install wandb --upgrade


In [3]:
artifact = run.use_artifact("exercise_4/genres_mod.parquet:latest")
local_path = artifact.file()
print(local_path)

./artifacts/genres_mod.parquet:v0/genres_mod.parquet


wandb: Network error (ConnectionError), entering retry loop. See wandb/debug-internal.log for full traceback.
wandb: Network error resolved after 1:23:10.835722, resuming normal operation.
wandb: Network error (ConnectionError), entering retry loop. See wandb/debug-internal.log for full traceback.
wandb: Network error resolved after 0:17:48.323970, resuming normal operation.
wandb: Network error (ConnectionError), entering retry loop. See wandb/debug-internal.log for full traceback.
wandb: Network error resolved after 0:00:17.092287, resuming normal operation.
wandb: Network error (ConnectionError), entering retry loop. See wandb/debug-internal.log for full traceback.
wandb: Network error resolved after 1:03:02.520271, resuming normal operation.
wandb: Network error (ConnectionError), entering retry loop. See wandb/debug-internal.log for full traceback.
wandb: Network error resolved after 3:08:52.417053, resuming normal operation.
wandb: Network error (ConnectionError), entering retry 

In [4]:
df = pd.read_parquet(local_path)
df.head()

danceability  energy  key  loudness  mode  speechiness  acousticness  \
0         0.831   0.814    2    -7.364     1       0.4200        0.0598   
1         0.719   0.493    8    -7.230     1       0.0794        0.4010   
2         0.850   0.893    5       NaN     1       0.0623        0.0138   
3         0.476   0.781    0    -4.710     1       0.1030        0.0237   
4         0.798   0.624    2    -7.668     1       0.2930        0.2170   

   instrumentalness  liveness  valence    tempo            type  duration_ms  \
0          0.013400    0.0556   0.3890  156.985  audio_features       124539   
1          0.000000    0.1180   0.1240  115.080  audio_features       224427   
2          0.000004    0.3720   0.0391  218.050  audio_features        98821   
3          0.000000    0.1140   0.1750  186.948  audio_features       123661   
4          0.000000    0.1660   0.5910  147.988  audio_features       123298   

   time_signature      genre                                      song_name  \
0               4  Dark Trap                            Mercury: Retrograde   
1               4  Dark Trap                                      Pathology   
2               4  Dark Trap                                       Symbiote   
3               3  Dark Trap  ProductOfDrugs (Prod. The Virus and Antidote)   
4               4  Dark Trap                                          Venom   

  title  
0  None  
1  None  
2  None  
3  None  
4  None

In [5]:
# Generate a profile and note the warnings
from pandas_profiling import ProfileReport

profile = ProfileReport(df, title="Pandas Profiling Report", explorative=True)
profile.to_widgets()

Summarize dataset:   0%|          | 0/30 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

In [6]:
df = df.drop_duplicates().reset_index(drop=True)
df.head()

danceability  energy  key  loudness  mode  speechiness  acousticness  \
0         0.831   0.814    2    -7.364     1       0.4200        0.0598   
1         0.719   0.493    8    -7.230     1       0.0794        0.4010   
2         0.850   0.893    5       NaN     1       0.0623        0.0138   
3         0.476   0.781    0    -4.710     1       0.1030        0.0237   
4         0.798   0.624    2    -7.668     1       0.2930        0.2170   

   instrumentalness  liveness  valence    tempo            type  duration_ms  \
0          0.013400    0.0556   0.3890  156.985  audio_features       124539   
1          0.000000    0.1180   0.1240  115.080  audio_features       224427   
2          0.000004    0.3720   0.0391  218.050  audio_features        98821   
3          0.000000    0.1140   0.1750  186.948  audio_features       123661   
4          0.000000    0.1660   0.5910  147.988  audio_features       123298   

   time_signature      genre                                      song_name  \
0               4  Dark Trap                            Mercury: Retrograde   
1               4  Dark Trap                                      Pathology   
2               4  Dark Trap                                       Symbiote   
3               3  Dark Trap  ProductOfDrugs (Prod. The Virus and Antidote)   
4               4  Dark Trap                                          Venom   

  title  
0  None  
1  None  
2  None  
3  None  
4  None

In [7]:
# Let's perform a minimal feature enginnering. Let's create a new feature by concatenating them, 
# after replacing all missing values with the empty string:
df['title'].fillna(value='', inplace=True)
df['song_name'].fillna(value='', inplace=True)
df['text_feature'] = df['title'] + ' ' + df['song_name']

NOTE: this feature will have to go to the feature store. If you do not have a feature store, then you should not compute it here as part of the preprocessing step. Instead, you should compute it within the inference pipeline.

In [8]:
ProfileReport(df, title="Pandas Profiling Report", explorative=True)

Summarize dataset:   0%|          | 0/31 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
run.finish()